In [1]:
import numpy as np
import pandas as pd 
import os
import matplotlib.pyplot as plt
import seaborn as sns
import sklearn
from itertools import product
import time
!pip install kmodes
from kmodes.kmodes import KModes

df = pd.read_csv('DATA/Van_car_taxi_drivers_final.csv')


In [4]:
start_time = time.time()

from itertools import combinations
from sklearn import preprocessing
from kmodes.kmodes import KModes
# List of variable names
variables_name =  ['deviation', 'seniority_in_the_job_months', 'age', 'Quarter', 'time_workday', 'specific_physical_activity', 'injured_body_part', 'injury_description']

# Generate combinations of 3 to 6 variables
combinations_list = []
for r in range(4, 5):
    combinations_list.extend(combinations(variables_name, r))

# Empty DataFrame to store results
table = pd.DataFrame()

def tuple_to_list(t):
    new_list = []
    for element in t:
        new_list.append(element)
    return new_list

# Iterate over combinations
for selected_columns in combinations_list:
    # Select columns from 'variables' DataFrame based on the combination
    listavar = tuple_to_list(selected_columns)
    subgrup_1 = df[listavar]
    print(subgrup_1.shape[1])
    # Clustering code
    subgroup = subgrup_1.copy()
    from sklearn import preprocessing  
    le = preprocessing.LabelEncoder()
    subgroup_encoded = subgroup.apply(le.fit_transform)
    #to create the list to get the percenge of significant clusters
    l=[]
    # Iterate through cluster numbers
    for n_clusters in range(10, 16):
        # Clustering
        km = KModes(n_clusters=n_clusters, init='Cao', n_init=1, verbose=1)
        clusters = km.fit_predict(subgroup_encoded)

        # Combine with original data
        combined = pd.concat([subgroup.reset_index(), pd.DataFrame({'Cluster': clusters})], axis=1).drop('index', axis=1)

        # Create table
        table = pd.DataFrame(columns=range(n_clusters))

        # Fill in table with percentage of instances of each value in each cluster for each variable
        for var in subgroup.columns:
            by_cluster_value = combined.groupby(['Cluster', var]).size()
            percentages = by_cluster_value.groupby(level=0).apply(lambda x: x / x.sum() * 100)
            pivot_table = pd.pivot_table(percentages.reset_index(), index=var, columns='Cluster', values=0, fill_value=0)

            # Fill in table with percentage of instances for each value in each cluster
            for i, col in enumerate(pivot_table.columns):
                values = pivot_table[col].index.tolist()
                pct_values = pivot_table[col].tolist()
                for j, value in enumerate(values):
                    table.loc[value, i] = pct_values[j]
            # Add new column with variable names based on index
        table['VARIABLE'] = ''

        variable_mapping = {}

        for column in subgroup.columns:
            unique_values = subgroup[column].unique()
            variable_mapping[column] = unique_values

        for i, index_value in enumerate(table.index.values):
            for variable, values in variable_mapping.items():
                if index_value in values:
                    table.iloc[i, -1] = variable
                    break
        print(table)
        table = table.reset_index().rename(columns={'index': 'value'})
        table = table[['VARIABLE'] + list(table.columns[:-1])]
        #print(table)
        table = table.set_index('VARIABLE')       

        # Add a new row for the cluster drivers percentage
        table.loc['Cluster percentage of accidents'] = 0
        # Calculate the number of instances in each cluster
        cluster_counts = combined['Cluster'].value_counts()

        # Fill in the table with the percentage of instances in each cluster
        for i, count in cluster_counts.items():
            table.loc['Cluster percentage of accidents', i] = count / len(combined) * 100            
        #table.to_excel(f'table_{n_clusters}_clusters_pas1.xlsx', index=True)
        table1=table
        # Save table to CSV file
        table = table.drop('value', axis=1)
        new_table_2 = pd.DataFrame(index=table.index.unique())
    # Iterate over each column (0, 1, 2, 3) and find the highest percentage for each variable
        for col in table.columns:
            col_max = table.groupby(level=0)[col].max()
            new_table_2[col] = col_max
    # Add the 'Cluster percentage of accidents' row back to the new DataFrame
        new_table_2.loc['Cluster percentage of accidents'] = table.loc['Cluster percentage of accidents']
    # Display the new DataFrame
        #print(new_table_2)
        #new_table_2.to_excel(f'table_{n_clusters}_clusters_pas2.xlsx', index=True)
        new_table_3= new_table_2.loc[new_table_2.index != 'Cluster percentage of accidents'] = (new_table_2.loc[new_table_2.index != 'Cluster percentage of accidents'] >= 75).astype(int)
        new_table_3.loc['VARIABLES => 75%'] = new_table_3.sum()
        #new_table_2.to_excel(f'table_{n_clusters}_clusters_pas3.xlsx', index=True)
        #print(new_table_3)
        print(subgrup_1.shape[1])  
        new_table_3.loc['Cluster Value'] = new_table_3 .loc['VARIABLES => 75%'] / subgrup_1.shape[1]
        new_table_3.loc['Cluster adequate?'] = new_table_3 .loc['Cluster Value']>=0.5
        new_table_4=new_table_3
        new_table_4.loc['Cluster percentage of accidents'] = table.loc['Cluster percentage of accidents']
        new_table_4.loc['SCORE'] = np.nan
        new_table_4.loc['SCORE' ,'TOTAL CLUSTERIZATION VALUE'] = new_table_4.loc['Cluster adequate?'].sum() / n_clusters

        if new_table_4.loc['Cluster adequate?'].sum() / n_clusters >= 0.80:
            table1.to_excel(f'table_{n_clusters}_clusters_{"".join(selected_columns)}.xlsx', index=True)
     #   print(n_clusters)   #######

end_time = time.time()

# Calculate the elapsed time
elapsed_time = end_time - start_time
print("Elapsed Time:", elapsed_time, "seconds")

4
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run 1, iteration: 1/100, moves: 0, cost: 127372.0
                                                           0         1  \
Breakage, bursting, slipping, falling, collapsi...   3.63273   4.28291   
Electrical problem, explosion, fire                 0.336067  0.385069   
Falling persons – Slip or trip and fall              11.4783   11.3242   
Loss of total or partial control of work equipm...   14.3229   55.5678   
Movement of the body as a result of or with phy...    49.882   4.73084   
Movement of the body without added physical effort   12.2545    15.222   
Other deviations                                     4.30486    4.8723   
Overflow, overturning, leak, spill, emanation       0.760152  0.840864   
Surprise, fear, violence, aggression, threat, p...   3.02861   2.77407   
Experienced                                          17.7395   59.3006   
Junior employees                                     1

<ipython-input-4-84fe52ef9226>:71: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                           0         1  \
Breakage, bursting, slipping, falling, collapsi...   3.53151   4.22254   
Electrical problem, explosion, fire                 0.293947  0.488275   
Falling persons – Slip or trip and fall              7.58052   10.0199   
Loss of total or partial control of work equipm...   20.5846   55.2851   
Movement of the body as a result of or with phy...   51.6933     9.401   
Movement of the body without added physical effort   8.60313   12.0074   
Other deviations                                      4.1194   4.86211   
Overflow, overturning, leak, spill, emanation       0.786619  0.797744   
Surprise, fear, violence, aggression, threat, p...   2.80699   2.91589   
Experienced                                          15.1486   55.2507   
Junior employees                                     14.4779   19.1527   
New hires                                            59.6423   15.7004   
Veterans                              

<ipython-input-4-84fe52ef9226>:71: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                           0         1  \
Breakage, bursting, slipping, falling, collapsi...    3.5801   4.54075   
Electrical problem, explosion, fire                 0.286938   0.52507   
Falling persons – Slip or trip and fall               4.4983   6.35261   
Loss of total or partial control of work equipm...   21.9485   56.3378   
Movement of the body as a result of or with phy...   52.8142   10.1095   
Movement of the body without added physical effort   9.17318   12.9123   
Other deviations                                     4.06569   5.22852   
Overflow, overturning, leak, spill, emanation       0.772525  0.857861   
Surprise, fear, violence, aggression, threat, p...   2.86055   3.13563   
Experienced                                          16.1524   56.6336   
Junior employees                                     10.4754   15.8409   
New hires                                              61.93   16.8836   
Veterans                              

...

                                                            0           1  \
1                                                     73.2431     3.76361   
2                                                     4.56561     15.4332   
3                                                     3.74119     4.83667   
4                                                     18.4501     75.9665   
Being present                                        0.881283     1.12829   
Driving/being on board a means of transport or ...    61.4055     6.76976   
Machine operations                                   0.557198    0.662774   
Manual transportation                                 6.51012     22.0372   
Movement                                              17.3016      50.213   
Object manipulation                                   11.6784     16.8613   
Work with hand tools                                 0.909711     1.32555   
other activities                                     0.756197     1.00205   

<ipython-input-4-84fe52ef9226>:71: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                            0           1  \
1                                                     85.7314     3.78752   
2                                                     5.34407     15.5312   
3                                                     4.37908      4.8674   
4                                                     4.54545     75.8139   
Being present                                         1.03155    0.849611   
Driving/being on board a means of transport or ...     54.825     6.81277   
Machine operations                                   0.652203    0.579641   
Manual transportation                                 7.62013     22.1772   
Movement                                              20.2516      50.532   
Object manipulation                                   13.6696     16.9684   
Work with hand tools                                  1.06482     1.27839   
other activities                                     0.885132    0.801969   

<ipython-input-4-84fe52ef9226>:71: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                            0          1  \
1                                                     85.7314    4.25589   
2                                                     5.34407    5.08565   
3                                                     4.37908    5.46931   
4                                                     4.54545    85.1892   
Being present                                         1.03155   0.740542   
Driving/being on board a means of transport or ...     54.825    7.65525   
Machine operations                                   0.652203   0.499643   
Manual transportation                                 7.62013    13.4458   
Movement                                              20.2516    56.7809   
Object manipulation                                   13.6696    19.0667   
Work with hand tools                                  1.06482    1.14204   
other activities                                     0.885132   0.669165   
Back, includ

In [54]:
#['deviation','specific_physical_activity','injured_body_part','injury_description','age','time_workday']
value_counts = df['time_workday'].value_counts()
percentage = (value_counts / len(df)) * 100
print(percentage)

worked 3 to 6 hours         48.813294
just started working        32.429593
worked more than 6 hours    18.757113
Name: time_workday, dtype: float64
